## SDK code to create CUSTOMER_vs_OVERALL_Avg_of_INVOICE_Count_of_item_28d

Feature description:
>Similarity between the customer and all customers measured by the Ratio of the Avg of INVOICE_Count_of_item over 28d for both entities.

In [ ]:
import featurebyte as fb
fb.use_profile("tutorial")

### Activate catalog

 See [SDK reference for catalogs](https://docs.featurebyte.com/latest/reference/core/catalog/)

In [ ]:
catalog = fb.Catalog.activate("Grocery Dataset Tutorial")

### Set windows for aggregation

In [ ]:
windows = ['28d']

### Get view from table
 See [SDK reference for views](https://docs.featurebyte.com/latest/reference/core/view/)

In [ ]:
# Get view from GROCERYINVOICE event table.
groceryinvoice_view = catalog.get_view("GROCERYINVOICE")

In [ ]:
# Get view from INVOICEITEMS item table.
invoiceitems_view = catalog.get_view("INVOICEITEMS")

### Do aggregation by invoice in INVOICEITEMS
 See [SDK reference for features](https://docs.featurebyte.com/latest/reference/core/feature/)

 See [SDK reference to groupby a view](https://docs.featurebyte.com/latest/reference/featurebyte.api.view.GroupByMixin.groupby/)

 See [SDK reference to do aggregation by invoice](https://docs.featurebyte.com/latest/reference/featurebyte.api.groupby.GroupBy.aggregate/)

 See [list of aggregation operations](https://docs.featurebyte.com/latest/reference/featurebyte.enum.AggFunc/)

 See [SDK reference to add an aggregation by invoice to the event view](https://docs.featurebyte.com/latest/reference/featurebyte.api.event_view.EventView.add_feature/)

In [ ]:
# Group invoiceitems_view by invoice entity (GroceryInvoiceGuid).
invoiceitems_view_by_invoice =\
invoiceitems_view.groupby("GroceryInvoiceGuid")

In [ ]:
# Count the number of item for the invoice.
invoice_count_of_item =\
invoiceitems_view_by_invoice.aggregate(
    None, method=fb.AggFunc.COUNT,
    feature_name="INVOICE_Count_of_item"
)

In [ ]:
# Add INVOICE_Count_of_item feature to the GROCERYINVOICE view as a column.
groceryinvoice_view = groceryinvoice_view.add_feature(
    "INVOICE_Count_of_item",
    invoice_count_of_item
)

### Do window aggregation from GROCERYINVOICE
 See [SDK reference for features](https://docs.featurebyte.com/latest/reference/core/feature/)

 See [SDK reference to groupby a view](https://docs.featurebyte.com/latest/reference/featurebyte.api.view.GroupByMixin.groupby/)

 See [SDK reference to do aggregation over time](https://docs.featurebyte.com/latest/reference/featurebyte.api.groupby.GroupBy.aggregate_over/)

 See [SDK reference for feature group](https://docs.featurebyte.com/latest/reference/core/feature_group/)

 See [list of aggregation operations](https://docs.featurebyte.com/latest/reference/featurebyte.enum.AggFunc/)

In [ ]:
# Group GROCERYINVOICE view by customer entity (GroceryCustomerGuid).
groceryinvoice_view_by_customer =\
groceryinvoice_view.groupby(['GroceryCustomerGuid'])

In [ ]:
# Get Avg of INVOICE_Count_of_item for the customer over time.
feature_group =\
groceryinvoice_view_by_customer.aggregate_over(
    "INVOICE_Count_of_item", method="avg",
    feature_names=[
        "CUSTOMER_Avg_of_INVOICE_Count_of_item"
        + "_" + w for w in windows
    ],
    windows=windows
)
# Get CUSTOMER_Avg_of_INVOICE_Count_of_item_28d object from feature group.
customer_avg_of_invoice_count_of_item_28d =\
feature_group["CUSTOMER_Avg_of_INVOICE_Count_of_item_28d"]

In [ ]:
# Group GROCERYINVOICE view without any groupby key for aggregates on all data.
groceryinvoice_view_by_overall =\
groceryinvoice_view.groupby([])

In [ ]:
# Get Avg of INVOICE_Count_of_item over time.
feature_group =\
groceryinvoice_view_by_overall.aggregate_over(
    "INVOICE_Count_of_item", method="avg",
    feature_names=[
        "OVERALL_Avg_of_INVOICE_Count_of_item"
        + "_" + w for w in windows
    ],
    windows=windows
)
# Get OVERALL_Avg_of_INVOICE_Count_of_item_28d object from feature group.
overall_avg_of_invoice_count_of_item_28d =\
feature_group["OVERALL_Avg_of_INVOICE_Count_of_item_28d"]

### Derive Similarity feature across entities
 See [list of feature transforms](https://docs.featurebyte.com/latest/about/glossary/#feature-transforms)

In [ ]:
# Derive Similarity feature from Ratio of
# CUSTOMER_Avg_of_INVOICE_Count_of_item_28d
# to OVERALL_Avg_of_INVOICE_Count_of_item_28d
customer_vs_overall_avg_of_invoice_count_of_item_28d = (
    customer_avg_of_invoice_count_of_item_28d
    / overall_avg_of_invoice_count_of_item_28d
)
# Give a name to new feature
customer_vs_overall_avg_of_invoice_count_of_item_28d.name = \
"CUSTOMER_vs_OVERALL_Avg_of_INVOICE_Count_of_item_28d"

### Preview feature
 Read on [the feature primary entity concept](https://docs.featurebyte.com/latest/about/glossary/#feature-primary-entity)

 Read on [the serving entity concept](https://docs.featurebyte.com/latest/about/glossary/#serving-entity)

 See [SDK reference for observation table](https://docs.featurebyte.com/latest/reference/core/observation_table/)

 See [SDK reference to preview feature](https://docs.featurebyte.com/latest/reference/featurebyte.api.feature.Feature.preview/)

In [ ]:
#Check the primary entity of the feature'
customer_vs_overall_avg_of_invoice_count_of_item_28d.primary_entity

In [ ]:
#Get observation table: 'Preview Table with 10 Customers'
preview_table = catalog.get_observation_table(
	"Preview Table with 10 Customers"
).to_pandas()

In [ ]:
#Preview CUSTOMER_vs_OVERALL_Avg_of_INVOICE_Count_of_item_28d
customer_vs_overall_avg_of_invoice_count_of_item_28d.preview(
	preview_table
)

### Save feature
 See [SDK reference to save feature](https://docs.featurebyte.com/latest/reference/featurebyte.api.feature.Feature.save/)

In [ ]:
# Save feature
customer_vs_overall_avg_of_invoice_count_of_item_28d.save()

### Add description and see feature definition file
 See [SDK reference for the definition file of a feature](https://docs.featurebyte.com/latest/reference/featurebyte.api.feature.Feature.definition/)

In [ ]:
# Add description
customer_vs_overall_avg_of_invoice_count_of_item_28d.update_description(
	"Similarity between the customer and all customers measured by the "
	"Ratio of the Avg of INVOICE_Count_of_item over 28d for both entities."
)
# See feature definition file
customer_vs_overall_avg_of_invoice_count_of_item_28d.definition